# Plotting demos
Demos the plotting functions and some related utility

In [1]:
import osmnx as ox
import networkx as nx
import numpy as np
import pandas as pd
import folium
import matplotlib.pyplot as plt

In [2]:
import os
os.chdir('../')

In [3]:
! pip install cenpy

In [4]:
from roc_bike_growth.loader import POI_graph_from_polygon, bike_infra_from_polygon, carall_from_polygon, _fill_edge_geometry, load_roc_proposed
from roc_bike_growth.plotting import add_categorical_legend
from roc_bike_growth.paper_gt import gt_with_existing_full
from roc_bike_growth.graph_utils import combine_nodes, graph_length_km
from roc_bike_growth.settings import CONFIG

/opt/conda/lib/python3.9/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [5]:
from roc_bike_growth.settings import CONFIG

## Load up everything

In [6]:
rochester = ox.geocode_to_gdf('rochester, ny').geometry[0]

In [7]:
bike_infra = bike_infra_from_polygon(rochester, compose_all=True)

In [8]:
proposed = load_roc_proposed()

In [9]:
existing_length = graph_length_km(bike_infra)

In [10]:
print(existing_length)

121.94828400000004


In [67]:
graph_length_km(proposed)

25.677638000000005

In [11]:
carall = carall_from_polygon(rochester, add_pois=True)
pois = nx.get_node_attributes(carall, 'poi').keys()

Exception at Port of Rochester, Lake Ave . This point will be dropped:
 Nominatim could not geocode query "Port of Rochester, Lake Ave  rochester ny"
Exception at 810-846 N GOODMAN ST. This point will be dropped:
 Nominatim could not geocode query "810-846 N GOODMAN ST rochester ny"
Exception at 650-672 E Main St. This point will be dropped:
 Nominatim could not geocode query "650-672 E Main St rochester ny"
Exception at 497-499 S. CLINTON. This point will be dropped:
 Nominatim could not geocode query "497-499 S. CLINTON rochester ny"


In [41]:
np.random.seed(1234)
carall_inc_adj = carall_from_polygon(rochester, add_pois=True, poi_downsample_pct=0.2)
pois_inc_adj = nx.get_node_attributes(carall_inc_adj, 'poi').keys()

Exception at Port of Rochester, Lake Ave . This point will be dropped:
 Nominatim could not geocode query "Port of Rochester, Lake Ave  rochester ny"
Exception at 810-846 N GOODMAN ST. This point will be dropped:
 Nominatim could not geocode query "810-846 N GOODMAN ST rochester ny"
Exception at 650-672 E Main St. This point will be dropped:
 Nominatim could not geocode query "650-672 E Main St rochester ny"
Exception at 497-499 S. CLINTON. This point will be dropped:
 Nominatim could not geocode query "497-499 S. CLINTON rochester ny"


/opt/conda/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/opt/conda/lib/python3.9/site-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/opt/conda/lib/python3.9/site-packages/cenpy/products.py:762: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  return self._from_name(county

In [13]:
poi_layer = folium.FeatureGroup(name='pois',show=True)
for node in pois:
    d = carall.nodes()[node]
    poi_layer.add_child(folium.CircleMarker(
        location=(d['y'],d['x']),
        radius=6,
        **{'color':'#e07a5f', 'fill':True}
    ))

In [48]:
poi_layer_adj = folium.FeatureGroup(name='pois_adj',show=True)
for node in pois_inc_adj:
    d = carall_inc_adj.nodes()[node]
    poi_layer_adj.add_child(folium.CircleMarker(
        location=(d['y'],d['x']),
        radius=6,
        **{'color':'blue', 'fill':True}
    ))

In [14]:
ROUTE_FACTOR = 0.25

## Compare income adj and no income adj

In [15]:
G_out = gt_with_existing_full(
    G_base = carall,
    G_existing = bike_infra,
    route_factor = ROUTE_FACTOR,
    prune_factor = 0.069,
    prune_measure = 'hybrid')


/home/jovyan/work/roc_bike_growth/paper_gt.py:32: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_nodes.append(G.get_shortest_paths(v, pois_indices[c:], output="vpath", weights = "mod_weight"))
/home/jovyan/work/roc_bike_growth/paper_gt.py:33: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_edges.append(G.get_shortest_paths(v, pois_indices[c:], output="epath", weights = "mod_weight"))


hybrid
502


In [28]:
G_out_inc_adj = gt_with_existing_full(
    G_base = carall_inc_adj,
    G_existing = bike_infra,
    route_factor = ROUTE_FACTOR,
    prune_factor = 0.065,
    prune_measure = 'hybrid')


hybrid
500


In [18]:
graph_length_km(proposed)

25.677638000000005

In [19]:
graph_length_km(G_out) - existing_length

25.68871099999997

In [29]:
graph_length_km(G_out_inc_adj) - existing_length

28.931708999999998

In [30]:
G_out_diff = nx.difference(combine_nodes(G_out, G_out_inc_adj), combine_nodes(G_out_inc_adj, G_out))
G_out_inc_adj_diff = nx.difference(combine_nodes(G_out_inc_adj, G_out), combine_nodes(G_out, G_out_inc_adj))
shared = nx.difference(nx.difference(combine_nodes(G_out, bike_infra),combine_nodes(bike_infra, G_out)), G_out_diff)


In [42]:
graph_length_km(ox.distance.add_edge_lengths(shared))

15.493429000000006

In [49]:
graphs = {
    '1. 25km no adj': G_out_diff,
    '2. 25km income adj': G_out_inc_adj_diff,
    '3. shared (1 and 2)': shared,
    '4. existing': bike_infra,
    '5. bikeable city proposed (25km)': proposed
}

colors = {
    '1. 25km no adj': 'orange',
    '2. 25km income adj':  'blue',
    '3. shared (1 and 2)': '#12EAEA',
    '4. existing': '#38bc53',
    '5. bikeable city proposed (25km)': 'red'
}

m = folium.Map(location=[43.1594283845703, -77.60641012519851], tiles="cartodbpositron", zoom_start=12)
for name, g in graphs.items():
    layer = folium.FeatureGroup(name=name,show=True)
    ox.folium.plot_graph_folium(
    g,
    layer, 
    # popup_attribute='name', 
     **{'color': colors.get(name)})
    layer.add_to(m)
    
poi_layer.add_to(m)
poi_layer_adj.add_to(m)

In [50]:
folium.LayerControl(position='bottomright').add_to(m)
add_categorical_legend(m, 'Infra type', colors.values(), colors.keys())

In [302]:
m.save('for_analysis.html')

## Look at network growth (hybrid, no inc adj)

In [57]:
existing_length

121.94828400000004

In [51]:
prune_factors = [0.05, 0.15, 0.35]
m = folium.Map(location=[43.1594283845703, -77.60641012519851], tiles="cartodbpositron", zoom_start=12)
for pf in prune_factors:
    graph = gt_with_existing_full(
        G_base = carall,
        G_existing = bike_infra,
        route_factor = ROUTE_FACTOR,
        prune_factor = pf,
        prune_measure = 'hybrid'
    )
    g_diff = nx.difference(combine_nodes(graph, bike_infra), combine_nodes(bike_infra, graph))
    print(graph_length_km(graph))
    layer = folium.FeatureGroup(
        name=f'km={graph_length_km(graph)-existing_length:{1}.{5}}',
        show=True)
    ox.folium.plot_graph_folium(
        g_diff,
        layer, 
        # popup_attribute='name', 
         **{'color': 'blue', 'opacity':0.33})
    layer.add_to(m)
    
existing = folium.FeatureGroup(name='existing',show=True)
ox.folium.plot_graph_folium(
    bike_infra,
    existing, 
    # popup_attribute='name', 
     **{'color': '#38bc53'})
existing.add_to(m)


/home/jovyan/work/roc_bike_growth/paper_gt.py:32: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_nodes.append(G.get_shortest_paths(v, pois_indices[c:], output="vpath", weights = "mod_weight"))
/home/jovyan/work/roc_bike_growth/paper_gt.py:33: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_edges.append(G.get_shortest_paths(v, pois_indices[c:], output="epath", weights = "mod_weight"))


hybrid
414
142.29940100000016


/home/jovyan/work/roc_bike_growth/paper_gt.py:32: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_nodes.append(G.get_shortest_paths(v, pois_indices[c:], output="vpath", weights = "mod_weight"))
/home/jovyan/work/roc_bike_growth/paper_gt.py:33: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_edges.append(G.get_shortest_paths(v, pois_indices[c:], output="epath", weights = "mod_weight"))


hybrid
factor: 40
102
factor: 40
53
factor: 40
62
factor: 20
32
factor: 20
36
factor: 20
36
factor: 10
13
factor: 10
10
factor: 10
10
factor: 10
19
factor: 5
5
factor: 5
15
factor: 2
2
factor: 2
6
factor: 2
8
factor: 1
3
factor: 1
3
factor: 1
3
810
182.1611850000002


/home/jovyan/work/roc_bike_growth/paper_gt.py:32: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_nodes.append(G.get_shortest_paths(v, pois_indices[c:], output="vpath", weights = "mod_weight"))
/home/jovyan/work/roc_bike_growth/paper_gt.py:33: RuntimeWarning: Couldn't reach some vertices at src/paths/dijkstra.c:441
  poi_edges.append(G.get_shortest_paths(v, pois_indices[c:], output="epath", weights = "mod_weight"))


hybrid
factor: 40
88
factor: 40
45
factor: 40
42
factor: 40
41
factor: 40
42
factor: 40
70
factor: 40
83
factor: 40
68
factor: 40
62
factor: 20
29
factor: 20
30
factor: 20
27
factor: 20
31
factor: 20
31
factor: 20
29
factor: 20
27
factor: 20
27
factor: 20
27
factor: 10
12
factor: 10
14
factor: 10
13
factor: 10
12
factor: 10
12
factor: 10
11
factor: 10
11
factor: 10
11
factor: 10
11
factor: 10
11
factor: 10
10
factor: 10
10
factor: 5
5
factor: 5
5
factor: 5
5
factor: 5
6
factor: 5
6
factor: 5
6
factor: 5
5
factor: 5
6
factor: 5
6
factor: 5
6
factor: 5
5
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 2
2
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1
1
factor: 1

In [52]:
folium.LayerControl(position='bottomright').add_to(m)
add_categorical_legend(
    m, 
    'Infra type', 
    ['blue' for pf in prune_factors] + ['#38bc53'], 
    [f'prune_factor={pf}' for pf in prune_factors] + ['existing']
)

In [ ]:
m.save("increasing_prune_hybrid.html")

In [52]:
g = gt_with_existing_full(
        G_base = carall,
        G_existing = bike_infra,
        route_factor = 0.5,
        prune_factor = 0.1)

betweenness


In [53]:
ox.plot_graph_folium(g)